# Grid Search for Bonston Housing dataset

In [1]:
# Load required libraries
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.utils.data

import numpy as np
import matplotlib.pyplot as plt
from sklearn.datasets import load_boston
from sklearn.model_selection import train_test_split

Halving learnig rates after 10.000 iterations.

In [2]:
# Set seed
np.random.seed(1)
torch.manual_seed(1)

# Load Boston Housing dataset
boston = load_boston(return_X_y=False)

# Split into training, validation and test set
X_train, X_test, y_train, y_test = train_test_split(boston.data, boston.target, test_size=50, random_state=1)
X_train, X_val, y_train, y_val = train_test_split(X_train, y_train, test_size=50, random_state=1)

# Convert arrays to Torch tensors
X_train = torch.FloatTensor(X_train)
y_train = torch.FloatTensor(y_train).view(-1,1)
X_val = torch.FloatTensor(X_val)
y_val = torch.FloatTensor(y_val).view(-1,1)
X_test = torch.FloatTensor(X_test)
y_test = torch.FloatTensor(y_test).view(-1,1)

# Normalise the training dataset
X_train_mean = X_train.mean(0)
X_train_std = X_train.std(0)
X_train_norm = X_train.add(-1, X_train_mean) / X_train_std
y_train_mean = torch.mean(y_train)
y_train_std = torch.std(y_train)
y_train_norm = y_train.add(-1, y_train_mean) / y_train_std

# Define the data-loader
train_data = torch.utils.data.TensorDataset(X_train_norm, y_train_norm)
train_loader = torch.utils.data.DataLoader(train_data, batch_size=32, num_workers=0)
val_data = torch.utils.data.TensorDataset(X_val, y_val)
val_loader = torch.utils.data.DataLoader(val_data, batch_size=50)
test_data = torch.utils.data.TensorDataset(X_test, y_test)
test_loader = torch.utils.data.DataLoader(test_data, batch_size=50)

In [3]:
# Fully connected Feed-Forward network with 2 hidden layers and SELU activations
if torch.cuda.is_available():
    device = torch.device("cuda")
else:
    device = torch.device("cpu")

class Model(nn.Module):

    def __init__(self):
        super(Model, self).__init__()
        self.model = nn.Sequential(
                      nn.Linear(13, 50, bias=True),
                      nn.SELU(),
                      nn.Linear(50, 50, bias=True),
                      nn.SELU(),
                      nn.Linear(50, 50, bias=True),
                      nn.SELU(),
                      nn.Linear(50,1, bias=True)
                    ).to(device)


    def forward(self, x):
        x = x.view(x.size(0), -1)
        x = self.model(x)
        return x

In [4]:
class evaluation(object):
    def __init__(self, test_data, n_samples, X_mean=None, X_std=None, y_mean=None, y_std=None):
        self.test_data = test_data
        self.X_mean = X_mean
        self.X_std = X_std
        self.y_mean = y_mean
        self.y_std = y_std
        self.n = 0
        self.avg_prediction = 0.
        self.sum_pp = 0.
        self.sumsqr_pp = 0.
        self.preds = torch.zeros(len(test_data.dataset),n_samples)

    def fn(self, model):

        with torch.autograd.no_grad():
            self.n += 1
            for x, y in iter(self.test_data):
                x = x.view(x.size(0), -1)

                if (self.X_mean is not None) & (self.X_std is not None):
                    x = (x - self.X_mean).float() / self.X_std

                standard_pred = model(x)

                if (self.y_mean is not None) & (self.y_std is not None):
                    standard_pred = standard_pred * self.y_std + self.y_mean
                
                self.preds[:,self.n-1] = standard_pred.view(-1,)
                self.avg_prediction = self.avg_prediction * (self.n - 1.) / self.n + standard_pred.view(-1,1) / self.n
                self.sum_pp += standard_pred
                self.sumsqr_pp += standard_pred * standard_pred
                std_pred = torch.sqrt((self.sumsqr_pp - (self.sum_pp * self.sum_pp) / self.n) / (self.n - 1))



                norm = torch.distributions.normal.Normal(y, std_pred)
                test_ll = norm.log_prob(self.avg_prediction).mean()



                error = nn.MSELoss(size_average=True)
                rmse = error(self.avg_prediction, y) ** 0.5

                return rmse, test_ll

## SGLD

In [10]:
# Load required libraries
import torch
import torchvision

from torch import nn
import torch.nn.functional as F
import numpy as np

import sgld
import model

# Set seed
np.random.seed(1)
torch.manual_seed(1)


# Network hyperparameters
lambda_ = 1.
# learning_rates = [9e-6, 8e-6, 7e-6, 6e-6, 5e-6, 4e-6, 3e-6, 2e-6, 1e-6, 9e-7, 8e-7]
# learning_rates = [1e-1, 1e-2, 1e-3, 1e-4, 1e-5, 1e-6, 1e-7, 1e-8]
learning_rates = [9e-5, 8e-5, 7e-5, 6e-5, 5e-5, 4e-5, 3e-5, 2e-5, 1e-5, 9e-6, 8e-6, 7e-6, 6e-6, 5e-6, 4e-6, 3e-6, 2e-6, 1e-6]
batch_size = 32.
dataset_size= 406.
# Number of samples to draw from the posterior distribution
n_samples = 300

# Initialise result array
val_llSGLD = np.zeros((1,len(learning_rates)))



for i in range(1):
    for j,lr in enumerate(learning_rates):
        network = Model()
        criterion = nn.MSELoss(size_average=False)
        optim = sgld.optim.sgld(network, lr, lambda_, batch_size, dataset_size)
        evaluate = evaluation(val_loader, n_samples, X_train_mean, X_train_std, y_train_mean, y_train_std)
        
        t = 1
        n = 0
        for epoch in range(2500):

            running_loss = 0
            for x, y in iter(train_loader):
                x = x.view(x.size(0), -1)

                network.zero_grad()
                output = network(x)
                loss = 0.5 * criterion(output, y)
                loss.backward()
                optim.step()



                running_loss += loss * batch_size / dataset_size

                # Sample from the posterior distribution
                if (t >= 300) & (t % 100 == 0) & (n < n_samples):
                    rmse, val_ll = evaluate.fn(network)
                    n += 1
                t += 1.
            print("lr {:.8f} - epoch {:d} - loss: {:.4f}".format(lr, epoch, running_loss))
        val_llSGLD[i,j] = val_ll

/home/mojo/anaconda3/lib/python3.6/site-packages/torch/nn/functional.py:52: UserWarning: size_average and reduce args will be deprecated, please use reduction='sum' instead.
  warnings.warn(warning.format(ret))


lr 0.00009000 - epoch 0 - loss: 10.2876
lr 0.00009000 - epoch 1 - loss: 6.1811
lr 0.00009000 - epoch 2 - loss: 5.3027
lr 0.00009000 - epoch 3 - loss: 5.1810
lr 0.00009000 - epoch 4 - loss: 4.9224
lr 0.00009000 - epoch 5 - loss: 4.6598
lr 0.00009000 - epoch 6 - loss: 4.7810
lr 0.00009000 - epoch 7 - loss: 4.7672
lr 0.00009000 - epoch 8 - loss: 4.2232
lr 0.00009000 - epoch 9 - loss: 3.8980
lr 0.00009000 - epoch 10 - loss: 3.8393
lr 0.00009000 - epoch 11 - loss: 3.8811
lr 0.00009000 - epoch 12 - loss: 4.1609
lr 0.00009000 - epoch 13 - loss: 4.7610
lr 0.00009000 - epoch 14 - loss: 4.3568
lr 0.00009000 - epoch 15 - loss: 4.1756
lr 0.00009000 - epoch 16 - loss: 4.1947
lr 0.00009000 - epoch 17 - loss: 7.0517
lr 0.00009000 - epoch 18 - loss: 4.3488
lr 0.00009000 - epoch 19 - loss: 3.9778
lr 0.00009000 - epoch 20 - loss: 9.2063
lr 0.00009000 - epoch 21 - loss: 3.8134
lr 0.00009000 - epoch 22 - loss: 4.1851
lr 0.00009000 - epoch 23 - loss: 3.7615
lr 0.00009000 - epoch 24 - loss: 4.9006
lr 0.0000

/home/mojo/anaconda3/lib/python3.6/site-packages/torch/nn/functional.py:52: UserWarning: size_average and reduce args will be deprecated, please use reduction='elementwise_mean' instead.
  warnings.warn(warning.format(ret))


lr 0.00009000 - epoch 28 - loss: 3.9520
lr 0.00009000 - epoch 29 - loss: 3.7025
lr 0.00009000 - epoch 30 - loss: 4.5841
lr 0.00009000 - epoch 31 - loss: 4.0372
lr 0.00009000 - epoch 32 - loss: 4.8992
lr 0.00009000 - epoch 33 - loss: 4.1181
lr 0.00009000 - epoch 34 - loss: 3.5435
lr 0.00009000 - epoch 35 - loss: 5.7012
lr 0.00009000 - epoch 36 - loss: 4.0651
lr 0.00009000 - epoch 37 - loss: 8.6187
lr 0.00009000 - epoch 38 - loss: 3.0284
lr 0.00009000 - epoch 39 - loss: 7.3230
lr 0.00009000 - epoch 40 - loss: 4.2843
lr 0.00009000 - epoch 41 - loss: 4.0374
lr 0.00009000 - epoch 42 - loss: 7.1638
lr 0.00009000 - epoch 43 - loss: 3.5731
lr 0.00009000 - epoch 44 - loss: 5.2952
lr 0.00009000 - epoch 45 - loss: 3.5014
lr 0.00009000 - epoch 46 - loss: 8.3723
lr 0.00009000 - epoch 47 - loss: 4.9532
lr 0.00009000 - epoch 48 - loss: 4.1065
lr 0.00009000 - epoch 49 - loss: 4.1249
lr 0.00009000 - epoch 50 - loss: 4.8567
lr 0.00009000 - epoch 51 - loss: 5.1778
lr 0.00009000 - epoch 52 - loss: 3.6937


lr 0.00009000 - epoch 232 - loss: 6.2448
lr 0.00009000 - epoch 233 - loss: 9.6898
lr 0.00009000 - epoch 234 - loss: 6.3739
lr 0.00009000 - epoch 235 - loss: 6.5026
lr 0.00009000 - epoch 236 - loss: 6.9431
lr 0.00009000 - epoch 237 - loss: 13.0610
lr 0.00009000 - epoch 238 - loss: 5.6163
lr 0.00009000 - epoch 239 - loss: 8.6937
lr 0.00009000 - epoch 240 - loss: 12.8064
lr 0.00009000 - epoch 241 - loss: 7.4661
lr 0.00009000 - epoch 242 - loss: 7.5747
lr 0.00009000 - epoch 243 - loss: 6.5219
lr 0.00009000 - epoch 244 - loss: 4.7377
lr 0.00009000 - epoch 245 - loss: 5.7165
lr 0.00009000 - epoch 246 - loss: 11.9214
lr 0.00009000 - epoch 247 - loss: 7.7565
lr 0.00009000 - epoch 248 - loss: 5.8200
lr 0.00009000 - epoch 249 - loss: 6.0424
lr 0.00009000 - epoch 250 - loss: 5.8770
lr 0.00009000 - epoch 251 - loss: 7.5304
lr 0.00009000 - epoch 252 - loss: 13.8623
lr 0.00009000 - epoch 253 - loss: 6.5903
lr 0.00009000 - epoch 254 - loss: 4.8322
lr 0.00009000 - epoch 255 - loss: 3.8908
lr 0.0000900

...

lr 0.00000100 - epoch 1669 - loss: 4.0179
lr 0.00000100 - epoch 1670 - loss: 4.0365
lr 0.00000100 - epoch 1671 - loss: 4.0291
lr 0.00000100 - epoch 1672 - loss: 4.0265
lr 0.00000100 - epoch 1673 - loss: 4.0190
lr 0.00000100 - epoch 1674 - loss: 4.0199
lr 0.00000100 - epoch 1675 - loss: 3.9957
lr 0.00000100 - epoch 1676 - loss: 3.9988
lr 0.00000100 - epoch 1677 - loss: 4.0217
lr 0.00000100 - epoch 1678 - loss: 4.0128
lr 0.00000100 - epoch 1679 - loss: 4.0532
lr 0.00000100 - epoch 1680 - loss: 4.0701
lr 0.00000100 - epoch 1681 - loss: 4.0449
lr 0.00000100 - epoch 1682 - loss: 4.0600
lr 0.00000100 - epoch 1683 - loss: 4.0543
lr 0.00000100 - epoch 1684 - loss: 4.0580
lr 0.00000100 - epoch 1685 - loss: 4.0594
lr 0.00000100 - epoch 1686 - loss: 4.0433
lr 0.00000100 - epoch 1687 - loss: 4.0237
lr 0.00000100 - epoch 1688 - loss: 4.0311
lr 0.00000100 - epoch 1689 - loss: 4.0515
lr 0.00000100 - epoch 1690 - loss: 4.0587
lr 0.00000100 - epoch 1691 - loss: 4.0859
lr 0.00000100 - epoch 1692 - loss:

lr 0.00000100 - epoch 1877 - loss: 3.7510
lr 0.00000100 - epoch 1878 - loss: 3.7831
lr 0.00000100 - epoch 1879 - loss: 3.7932
lr 0.00000100 - epoch 1880 - loss: 3.7922
lr 0.00000100 - epoch 1881 - loss: 3.7821
lr 0.00000100 - epoch 1882 - loss: 3.7747
lr 0.00000100 - epoch 1883 - loss: 3.7590
lr 0.00000100 - epoch 1884 - loss: 3.7539
lr 0.00000100 - epoch 1885 - loss: 3.7623
lr 0.00000100 - epoch 1886 - loss: 3.7665
lr 0.00000100 - epoch 1887 - loss: 3.7883
lr 0.00000100 - epoch 1888 - loss: 3.7988
lr 0.00000100 - epoch 1889 - loss: 3.7941
lr 0.00000100 - epoch 1890 - loss: 3.7911
lr 0.00000100 - epoch 1891 - loss: 3.7776
lr 0.00000100 - epoch 1892 - loss: 3.7664
lr 0.00000100 - epoch 1893 - loss: 3.7571
lr 0.00000100 - epoch 1894 - loss: 3.7557
lr 0.00000100 - epoch 1895 - loss: 3.7683
lr 0.00000100 - epoch 1896 - loss: 3.7808
lr 0.00000100 - epoch 1897 - loss: 3.8040
lr 0.00000100 - epoch 1898 - loss: 3.8399
lr 0.00000100 - epoch 1899 - loss: 3.8524
lr 0.00000100 - epoch 1900 - loss:

lr 0.00000100 - epoch 2080 - loss: 3.7756
lr 0.00000100 - epoch 2081 - loss: 3.7964
lr 0.00000100 - epoch 2082 - loss: 3.7883
lr 0.00000100 - epoch 2083 - loss: 3.7722
lr 0.00000100 - epoch 2084 - loss: 3.7669
lr 0.00000100 - epoch 2085 - loss: 3.7834
lr 0.00000100 - epoch 2086 - loss: 3.7551
lr 0.00000100 - epoch 2087 - loss: 3.7808
lr 0.00000100 - epoch 2088 - loss: 3.8259
lr 0.00000100 - epoch 2089 - loss: 3.8265
lr 0.00000100 - epoch 2090 - loss: 3.8640
lr 0.00000100 - epoch 2091 - loss: 3.8488
lr 0.00000100 - epoch 2092 - loss: 3.8300
lr 0.00000100 - epoch 2093 - loss: 3.8717
lr 0.00000100 - epoch 2094 - loss: 3.8539
lr 0.00000100 - epoch 2095 - loss: 3.8935
lr 0.00000100 - epoch 2096 - loss: 3.9443
lr 0.00000100 - epoch 2097 - loss: 3.9336
lr 0.00000100 - epoch 2098 - loss: 3.8795
lr 0.00000100 - epoch 2099 - loss: 3.8094
lr 0.00000100 - epoch 2100 - loss: 3.8348
lr 0.00000100 - epoch 2101 - loss: 3.8658
lr 0.00000100 - epoch 2102 - loss: 3.8635
lr 0.00000100 - epoch 2103 - loss:

lr 0.00000100 - epoch 2282 - loss: 3.6159
lr 0.00000100 - epoch 2283 - loss: 3.5902
lr 0.00000100 - epoch 2284 - loss: 3.5719
lr 0.00000100 - epoch 2285 - loss: 3.5205
lr 0.00000100 - epoch 2286 - loss: 3.5190
lr 0.00000100 - epoch 2287 - loss: 3.5249
lr 0.00000100 - epoch 2288 - loss: 3.5608
lr 0.00000100 - epoch 2289 - loss: 3.5381
lr 0.00000100 - epoch 2290 - loss: 3.5523
lr 0.00000100 - epoch 2291 - loss: 3.5563
lr 0.00000100 - epoch 2292 - loss: 3.5564
lr 0.00000100 - epoch 2293 - loss: 3.5591
lr 0.00000100 - epoch 2294 - loss: 3.5423
lr 0.00000100 - epoch 2295 - loss: 3.5488
lr 0.00000100 - epoch 2296 - loss: 3.5324
lr 0.00000100 - epoch 2297 - loss: 3.5037
lr 0.00000100 - epoch 2298 - loss: 3.4648
lr 0.00000100 - epoch 2299 - loss: 3.4855
lr 0.00000100 - epoch 2300 - loss: 3.5125
lr 0.00000100 - epoch 2301 - loss: 3.4891
lr 0.00000100 - epoch 2302 - loss: 3.5016
lr 0.00000100 - epoch 2303 - loss: 3.5220
lr 0.00000100 - epoch 2304 - loss: 3.5247
lr 0.00000100 - epoch 2305 - loss:

lr 0.00000100 - epoch 2478 - loss: 3.6024
lr 0.00000100 - epoch 2479 - loss: 3.6278
lr 0.00000100 - epoch 2480 - loss: 3.6316
lr 0.00000100 - epoch 2481 - loss: 3.6180
lr 0.00000100 - epoch 2482 - loss: 3.6209
lr 0.00000100 - epoch 2483 - loss: 3.6091
lr 0.00000100 - epoch 2484 - loss: 3.5908
lr 0.00000100 - epoch 2485 - loss: 3.6285
lr 0.00000100 - epoch 2486 - loss: 3.6270
lr 0.00000100 - epoch 2487 - loss: 3.6030
lr 0.00000100 - epoch 2488 - loss: 3.6090
lr 0.00000100 - epoch 2489 - loss: 3.6130
lr 0.00000100 - epoch 2490 - loss: 3.5913
lr 0.00000100 - epoch 2491 - loss: 3.5995
lr 0.00000100 - epoch 2492 - loss: 3.6045
lr 0.00000100 - epoch 2493 - loss: 3.6317
lr 0.00000100 - epoch 2494 - loss: 3.6342
lr 0.00000100 - epoch 2495 - loss: 3.6503
lr 0.00000100 - epoch 2496 - loss: 3.6651
lr 0.00000100 - epoch 2497 - loss: 3.6312
lr 0.00000100 - epoch 2498 - loss: 3.6218
lr 0.00000100 - epoch 2499 - loss: 3.6141


In [11]:
val_llSGLD
# 9e-6

array([[        nan,         nan,         nan, -2.44183922, -2.40198588,
        -2.46547198, -2.41869855, -2.39130664, -2.45101762, -2.36047149,
        -2.49434566, -2.37358999, -2.47035813, -2.42867565, -2.46679544,
        -2.7415328 , -2.68148255, -3.91511869]])

## pSGLD

In [15]:
import torch
import torchvision
import os

from itertools import chain
from torch import nn
from torchvision import transforms
import torch.nn.functional as F
import numpy as np

import psgld 

np.random.seed(1)
torch.manual_seed(1)





lambda_ = 1.
# learning_rates = [1e-1, 1e-2, 1e-3, 1e-4, 1e-5, 1e-6, 1e-7, 1e-8, 1e-9, 1e-10, 1e-11, 1e-12, 1e-13, 1e-14]
learning_rates = [9e-4, 8e-4, 7e-4, 6e-4, 5e-4, 4e-4, 3e-4, 2e-4, 1e-4, 9e-5, 8e-5, 7e-5, 6e-5, 5e-5, 4e-5, 3e-5, 2e-5, 1e-5]
# learning_rates = [1e-2, 9e-3, 8e-3, 7e-3, 6e-3, 5e-3, 4e-3, 2e-3, 1e-3]
alpha = 0.99


batch_size = 32
dataset_size= 406

n_chains = 10
n_samples = 300


val_llPSGLD = np.zeros((1,len(learning_rates)))


for i in range(1):
    for j,lr in enumerate(learning_rates):
        network = Model()
        criterion = nn.MSELoss(size_average=False)
        optim = psgld.optim.psgld(network, lr, alpha, lambda_, batch_size, dataset_size)
        evaluate = evaluation(val_loader, n_samples, X_train_mean, X_train_std, y_train_mean, y_train_std)

        t = 1
        n = 0
        for epoch in range(2500):

            running_loss = 0
            for x, y in iter(train_loader):
                x = x.view(x.size(0), -1)

                network.zero_grad()
                output = network(x)
                loss = 0.5 * criterion(output, y)
                loss.backward()
                optim.step()


                running_loss += loss * batch_size / dataset_size


                if (t >= 300) & (t % 100 == 0) & (n < n_samples):
                    rmse, val_ll = evaluate.fn(network)
                    n += 1
                t += 1.
            print("lr {:.8f} - epoch {:d} - loss: {:.4f}".format(lr, epoch, running_loss))
        val_llPSGLD[i,j] = val_ll

/home/mojo/anaconda3/lib/python3.6/site-packages/torch/nn/functional.py:52: UserWarning: size_average and reduce args will be deprecated, please use reduction='sum' instead.
  warnings.warn(warning.format(ret))


lr 0.00090000 - epoch 0 - loss: 8.0978
lr 0.00090000 - epoch 1 - loss: 5.5042
lr 0.00090000 - epoch 2 - loss: 4.7682
lr 0.00090000 - epoch 3 - loss: 4.6662
lr 0.00090000 - epoch 4 - loss: 5.1285
lr 0.00090000 - epoch 5 - loss: 4.9473
lr 0.00090000 - epoch 6 - loss: 4.9166
lr 0.00090000 - epoch 7 - loss: 4.7128
lr 0.00090000 - epoch 8 - loss: 5.1061
lr 0.00090000 - epoch 9 - loss: 4.4424
lr 0.00090000 - epoch 10 - loss: 4.5287
lr 0.00090000 - epoch 11 - loss: 4.5198
lr 0.00090000 - epoch 12 - loss: 4.4814
lr 0.00090000 - epoch 13 - loss: 5.3335
lr 0.00090000 - epoch 14 - loss: 5.0006
lr 0.00090000 - epoch 15 - loss: 4.4246
lr 0.00090000 - epoch 16 - loss: 4.9596
lr 0.00090000 - epoch 17 - loss: 5.1548
lr 0.00090000 - epoch 18 - loss: 4.7485
lr 0.00090000 - epoch 19 - loss: 5.0966
lr 0.00090000 - epoch 20 - loss: 5.0738
lr 0.00090000 - epoch 21 - loss: 5.1902
lr 0.00090000 - epoch 22 - loss: 4.4351
lr 0.00090000 - epoch 23 - loss: 4.6534
lr 0.00090000 - epoch 24 - loss: 5.4586
lr 0.00090

/home/mojo/anaconda3/lib/python3.6/site-packages/torch/nn/functional.py:52: UserWarning: size_average and reduce args will be deprecated, please use reduction='elementwise_mean' instead.
  warnings.warn(warning.format(ret))


lr 0.00090000 - epoch 26 - loss: 4.5765
lr 0.00090000 - epoch 27 - loss: 5.0230
lr 0.00090000 - epoch 28 - loss: 5.0507
lr 0.00090000 - epoch 29 - loss: 4.1467
lr 0.00090000 - epoch 30 - loss: 4.6212
lr 0.00090000 - epoch 31 - loss: 4.7228
lr 0.00090000 - epoch 32 - loss: 5.3965
lr 0.00090000 - epoch 33 - loss: 5.6445
lr 0.00090000 - epoch 34 - loss: 5.1034
lr 0.00090000 - epoch 35 - loss: 5.1225
lr 0.00090000 - epoch 36 - loss: 4.1961
lr 0.00090000 - epoch 37 - loss: 4.6791
lr 0.00090000 - epoch 38 - loss: 4.1691
lr 0.00090000 - epoch 39 - loss: 4.1888
lr 0.00090000 - epoch 40 - loss: 4.4735
lr 0.00090000 - epoch 41 - loss: 4.5082
lr 0.00090000 - epoch 42 - loss: 4.2762
lr 0.00090000 - epoch 43 - loss: 4.3922
lr 0.00090000 - epoch 44 - loss: 4.0616
lr 0.00090000 - epoch 45 - loss: 4.7091
lr 0.00090000 - epoch 46 - loss: 4.6683
lr 0.00090000 - epoch 47 - loss: 4.2729
lr 0.00090000 - epoch 48 - loss: 3.9829
lr 0.00090000 - epoch 49 - loss: 3.5625
lr 0.00090000 - epoch 50 - loss: 4.1609


lr 0.00090000 - epoch 234 - loss: 4.5207
lr 0.00090000 - epoch 235 - loss: 5.7935
lr 0.00090000 - epoch 236 - loss: 5.0095
lr 0.00090000 - epoch 237 - loss: 5.9987
lr 0.00090000 - epoch 238 - loss: 5.4566
lr 0.00090000 - epoch 239 - loss: 5.3316
lr 0.00090000 - epoch 240 - loss: 4.9890
lr 0.00090000 - epoch 241 - loss: 5.0050
lr 0.00090000 - epoch 242 - loss: 5.9604
lr 0.00090000 - epoch 243 - loss: 5.6938
lr 0.00090000 - epoch 244 - loss: 5.0491
lr 0.00090000 - epoch 245 - loss: 5.0094
lr 0.00090000 - epoch 246 - loss: 5.6612
lr 0.00090000 - epoch 247 - loss: 5.5503
lr 0.00090000 - epoch 248 - loss: 4.6803
lr 0.00090000 - epoch 249 - loss: 5.6305
lr 0.00090000 - epoch 250 - loss: 5.6328
lr 0.00090000 - epoch 251 - loss: 5.9863
lr 0.00090000 - epoch 252 - loss: 5.8391
lr 0.00090000 - epoch 253 - loss: 6.0677
lr 0.00090000 - epoch 254 - loss: 5.2319
lr 0.00090000 - epoch 255 - loss: 5.3588
lr 0.00090000 - epoch 256 - loss: 5.2496
lr 0.00090000 - epoch 257 - loss: 4.9180
lr 0.00090000 - 

...

lr 0.00001000 - epoch 1557 - loss: 4.0504
lr 0.00001000 - epoch 1558 - loss: 4.0749
lr 0.00001000 - epoch 1559 - loss: 4.0643
lr 0.00001000 - epoch 1560 - loss: 4.1334
lr 0.00001000 - epoch 1561 - loss: 4.1841
lr 0.00001000 - epoch 1562 - loss: 4.1753
lr 0.00001000 - epoch 1563 - loss: 4.1999
lr 0.00001000 - epoch 1564 - loss: 4.2234
lr 0.00001000 - epoch 1565 - loss: 4.1831
lr 0.00001000 - epoch 1566 - loss: 4.2241
lr 0.00001000 - epoch 1567 - loss: 4.1734
lr 0.00001000 - epoch 1568 - loss: 4.2144
lr 0.00001000 - epoch 1569 - loss: 4.1599
lr 0.00001000 - epoch 1570 - loss: 4.1331
lr 0.00001000 - epoch 1571 - loss: 4.1682
lr 0.00001000 - epoch 1572 - loss: 4.2040
lr 0.00001000 - epoch 1573 - loss: 4.2157
lr 0.00001000 - epoch 1574 - loss: 4.2341
lr 0.00001000 - epoch 1575 - loss: 4.2325
lr 0.00001000 - epoch 1576 - loss: 4.2008
lr 0.00001000 - epoch 1577 - loss: 4.2169
lr 0.00001000 - epoch 1578 - loss: 4.2584
lr 0.00001000 - epoch 1579 - loss: 4.3014
lr 0.00001000 - epoch 1580 - loss:

lr 0.00001000 - epoch 1756 - loss: 3.8323
lr 0.00001000 - epoch 1757 - loss: 3.8113
lr 0.00001000 - epoch 1758 - loss: 3.8202
lr 0.00001000 - epoch 1759 - loss: 3.8457
lr 0.00001000 - epoch 1760 - loss: 3.8061
lr 0.00001000 - epoch 1761 - loss: 3.8068
lr 0.00001000 - epoch 1762 - loss: 3.7542
lr 0.00001000 - epoch 1763 - loss: 3.7628
lr 0.00001000 - epoch 1764 - loss: 3.7573
lr 0.00001000 - epoch 1765 - loss: 3.7738
lr 0.00001000 - epoch 1766 - loss: 3.7467
lr 0.00001000 - epoch 1767 - loss: 3.7120
lr 0.00001000 - epoch 1768 - loss: 3.6995
lr 0.00001000 - epoch 1769 - loss: 3.6820
lr 0.00001000 - epoch 1770 - loss: 3.6587
lr 0.00001000 - epoch 1771 - loss: 3.7039
lr 0.00001000 - epoch 1772 - loss: 3.7000
lr 0.00001000 - epoch 1773 - loss: 3.6665
lr 0.00001000 - epoch 1774 - loss: 3.6527
lr 0.00001000 - epoch 1775 - loss: 3.6442
lr 0.00001000 - epoch 1776 - loss: 3.6449
lr 0.00001000 - epoch 1777 - loss: 3.6315
lr 0.00001000 - epoch 1778 - loss: 3.6283
lr 0.00001000 - epoch 1779 - loss:

lr 0.00001000 - epoch 1952 - loss: 3.7273
lr 0.00001000 - epoch 1953 - loss: 3.7362
lr 0.00001000 - epoch 1954 - loss: 3.7303
lr 0.00001000 - epoch 1955 - loss: 3.7625
lr 0.00001000 - epoch 1956 - loss: 3.7715
lr 0.00001000 - epoch 1957 - loss: 3.7941
lr 0.00001000 - epoch 1958 - loss: 3.7780
lr 0.00001000 - epoch 1959 - loss: 3.8128
lr 0.00001000 - epoch 1960 - loss: 3.7947
lr 0.00001000 - epoch 1961 - loss: 3.7330
lr 0.00001000 - epoch 1962 - loss: 3.7441
lr 0.00001000 - epoch 1963 - loss: 3.7373
lr 0.00001000 - epoch 1964 - loss: 3.7299
lr 0.00001000 - epoch 1965 - loss: 3.7285
lr 0.00001000 - epoch 1966 - loss: 3.8041
lr 0.00001000 - epoch 1967 - loss: 3.8413
lr 0.00001000 - epoch 1968 - loss: 3.8343
lr 0.00001000 - epoch 1969 - loss: 3.8163
lr 0.00001000 - epoch 1970 - loss: 3.8320
lr 0.00001000 - epoch 1971 - loss: 3.8161
lr 0.00001000 - epoch 1972 - loss: 3.7860
lr 0.00001000 - epoch 1973 - loss: 3.7552
lr 0.00001000 - epoch 1974 - loss: 3.8207
lr 0.00001000 - epoch 1975 - loss:

lr 0.00001000 - epoch 2148 - loss: 3.6751
lr 0.00001000 - epoch 2149 - loss: 3.6977
lr 0.00001000 - epoch 2150 - loss: 3.7723
lr 0.00001000 - epoch 2151 - loss: 3.7824
lr 0.00001000 - epoch 2152 - loss: 3.7800
lr 0.00001000 - epoch 2153 - loss: 3.8014
lr 0.00001000 - epoch 2154 - loss: 3.7473
lr 0.00001000 - epoch 2155 - loss: 3.7429
lr 0.00001000 - epoch 2156 - loss: 3.7610
lr 0.00001000 - epoch 2157 - loss: 3.7719
lr 0.00001000 - epoch 2158 - loss: 3.8233
lr 0.00001000 - epoch 2159 - loss: 3.8182
lr 0.00001000 - epoch 2160 - loss: 3.8253
lr 0.00001000 - epoch 2161 - loss: 3.7935
lr 0.00001000 - epoch 2162 - loss: 3.7864
lr 0.00001000 - epoch 2163 - loss: 3.7918
lr 0.00001000 - epoch 2164 - loss: 3.7741
lr 0.00001000 - epoch 2165 - loss: 3.7359
lr 0.00001000 - epoch 2166 - loss: 3.6929
lr 0.00001000 - epoch 2167 - loss: 3.7048
lr 0.00001000 - epoch 2168 - loss: 3.6173
lr 0.00001000 - epoch 2169 - loss: 3.5606
lr 0.00001000 - epoch 2170 - loss: 3.6041
lr 0.00001000 - epoch 2171 - loss:

lr 0.00001000 - epoch 2345 - loss: 3.6661
lr 0.00001000 - epoch 2346 - loss: 3.6271
lr 0.00001000 - epoch 2347 - loss: 3.5827
lr 0.00001000 - epoch 2348 - loss: 3.5612
lr 0.00001000 - epoch 2349 - loss: 3.5709
lr 0.00001000 - epoch 2350 - loss: 3.5812
lr 0.00001000 - epoch 2351 - loss: 3.6093
lr 0.00001000 - epoch 2352 - loss: 3.6154
lr 0.00001000 - epoch 2353 - loss: 3.6277
lr 0.00001000 - epoch 2354 - loss: 3.6376
lr 0.00001000 - epoch 2355 - loss: 3.6244
lr 0.00001000 - epoch 2356 - loss: 3.5905
lr 0.00001000 - epoch 2357 - loss: 3.5624
lr 0.00001000 - epoch 2358 - loss: 3.5632
lr 0.00001000 - epoch 2359 - loss: 3.5464
lr 0.00001000 - epoch 2360 - loss: 3.5383
lr 0.00001000 - epoch 2361 - loss: 3.5815
lr 0.00001000 - epoch 2362 - loss: 3.5782
lr 0.00001000 - epoch 2363 - loss: 3.5920
lr 0.00001000 - epoch 2364 - loss: 3.5945
lr 0.00001000 - epoch 2365 - loss: 3.6089
lr 0.00001000 - epoch 2366 - loss: 3.6276
lr 0.00001000 - epoch 2367 - loss: 3.6756
lr 0.00001000 - epoch 2368 - loss:

In [16]:
val_llPSGLD
#7e-5

array([[-2.60722923, -2.54174161, -2.59113121, -2.53823519, -2.56032467,
        -2.51946115, -2.59904003, -2.64212775, -2.55822778, -2.62919807,
        -2.58829212, -2.41333914, -2.5689857 , -2.72027397, -2.64264989,
        -2.54549432, -2.79171395, -2.73217463]])

## K-SGLD

In [5]:
import torch
#import torchvision
import os

from itertools import chain
from torch import nn
#from torchvision import transforms
import torch.nn.functional as F
import numpy as np
#from numpy.random import RandomState

import ksgld


np.random.seed(1)
torch.manual_seed(1)



batch_size = 32
dataset_size=406

n_chains = 10
n_samples = 300



# learning_rates = [1e-3, 1e-4, 1e-5, 1e-6, 1e-7, 1e-8]
#5e-4
#6e-4
#2e-4
#8e-4]
# learning_rates = [1e-3, 9e-4, 8e-4, 7e-4, 6e-4, 5e-4]
learning_rates = [1e-3, 9e-4, 8e-4, 7e-4, 6e-4, 5e-4, 4e-4, 3e-4, 2e-4, 1e-4]


val_llKSGLD = np.zeros((1,len(learning_rates)))


for i in range(1):
    for j,lr in enumerate(learning_rates):
        network = Model()
        criterion = nn.MSELoss(size_average=False)
        optim = ksgld.optim.KSGLD(network, criterion, batch_size, dataset_size, eta=1., v=0., lambda_=1., epsilon=lr, l2=1e-3, invert_every=1)
        evaluate = evaluation(val_loader, n_samples, X_train_mean, X_train_std, y_train_mean, y_train_std)

        t = 1.
        n = 0


        for epoch in range(2500):
            running_loss = 0
            for x, y in iter(train_loader):
                x = x.view(x.size(0), -1)

                optim.update_curvature(x)

                network.zero_grad()
                output = network(x)
                loss = 0.5 * criterion(output, y)
                loss.backward()
                optim.step()

                running_loss += loss * batch_size / dataset_size

                if (t >= 300) & (t % 100 == 0) & (n < n_samples):
                    rmse, val_ll = evaluate.fn(network)
                    n += 1
                t += 1.
            print("lr {:.8f} - epoch {:d} - loss: {:.4f}".format(lr, epoch, running_loss))
        val_llKSGLD[i,j] = val_ll

/home/mojo/anaconda3/lib/python3.6/site-packages/torch/nn/functional.py:52: UserWarning: size_average and reduce args will be deprecated, please use reduction='sum' instead.
  warnings.warn(warning.format(ret))
/home/mojo/anaconda3/lib/python3.6/site-packages/torch/nn/functional.py:52: UserWarning: size_average and reduce args will be deprecated, please use reduction='none' instead.
  warnings.warn(warning.format(ret))


lr 0.00100000 - epoch 0 - loss: 8.4606
lr 0.00100000 - epoch 1 - loss: 10.6655
lr 0.00100000 - epoch 2 - loss: 8.1222
lr 0.00100000 - epoch 3 - loss: 8.4952
lr 0.00100000 - epoch 4 - loss: 7.8426
lr 0.00100000 - epoch 5 - loss: 5.3445
lr 0.00100000 - epoch 6 - loss: 4.9158
lr 0.00100000 - epoch 7 - loss: 5.7857
lr 0.00100000 - epoch 8 - loss: 5.3195
lr 0.00100000 - epoch 9 - loss: 5.3266
lr 0.00100000 - epoch 10 - loss: 6.0448
lr 0.00100000 - epoch 11 - loss: 4.3905
lr 0.00100000 - epoch 12 - loss: 7.4815
lr 0.00100000 - epoch 13 - loss: 3.6922
lr 0.00100000 - epoch 14 - loss: 3.9133
lr 0.00100000 - epoch 15 - loss: 3.8652
lr 0.00100000 - epoch 16 - loss: 5.1341
lr 0.00100000 - epoch 17 - loss: 3.7999
lr 0.00100000 - epoch 18 - loss: 4.7440
lr 0.00100000 - epoch 19 - loss: 2.9073
lr 0.00100000 - epoch 20 - loss: 3.3763
lr 0.00100000 - epoch 21 - loss: 4.9779
lr 0.00100000 - epoch 22 - loss: 3.5601


/home/mojo/anaconda3/lib/python3.6/site-packages/torch/nn/functional.py:52: UserWarning: size_average and reduce args will be deprecated, please use reduction='elementwise_mean' instead.
  warnings.warn(warning.format(ret))


lr 0.00100000 - epoch 23 - loss: 3.3206
lr 0.00100000 - epoch 24 - loss: 3.3203
lr 0.00100000 - epoch 25 - loss: 3.4738
lr 0.00100000 - epoch 26 - loss: 3.3673
lr 0.00100000 - epoch 27 - loss: 2.7305
lr 0.00100000 - epoch 28 - loss: 3.2163
lr 0.00100000 - epoch 29 - loss: 2.5021
lr 0.00100000 - epoch 30 - loss: 2.5197
lr 0.00100000 - epoch 31 - loss: 3.1721
lr 0.00100000 - epoch 32 - loss: 3.0038
lr 0.00100000 - epoch 33 - loss: 2.0468
lr 0.00100000 - epoch 34 - loss: 2.8773
lr 0.00100000 - epoch 35 - loss: 3.0083
lr 0.00100000 - epoch 36 - loss: 3.0356
lr 0.00100000 - epoch 37 - loss: 2.6497
lr 0.00100000 - epoch 38 - loss: 2.6415
lr 0.00100000 - epoch 39 - loss: 2.5787
lr 0.00100000 - epoch 40 - loss: 2.5519
lr 0.00100000 - epoch 41 - loss: 2.6524
lr 0.00100000 - epoch 42 - loss: 2.3578
lr 0.00100000 - epoch 43 - loss: 2.7529
lr 0.00100000 - epoch 44 - loss: 2.2256
lr 0.00100000 - epoch 45 - loss: 1.7847
lr 0.00100000 - epoch 46 - loss: 2.5429
lr 0.00100000 - epoch 47 - loss: 2.1973


lr 0.00100000 - epoch 225 - loss: 2.0256
lr 0.00100000 - epoch 226 - loss: 2.4254
lr 0.00100000 - epoch 227 - loss: 4.1442
lr 0.00100000 - epoch 228 - loss: 2.8011
lr 0.00100000 - epoch 229 - loss: 1.8688
lr 0.00100000 - epoch 230 - loss: 3.0235
lr 0.00100000 - epoch 231 - loss: 5.6053
lr 0.00100000 - epoch 232 - loss: 5.6463
lr 0.00100000 - epoch 233 - loss: 3.1154
lr 0.00100000 - epoch 234 - loss: 1.8739
lr 0.00100000 - epoch 235 - loss: 1.9278
lr 0.00100000 - epoch 236 - loss: 2.9703
lr 0.00100000 - epoch 237 - loss: 2.7485
lr 0.00100000 - epoch 238 - loss: 2.7909
lr 0.00100000 - epoch 239 - loss: 2.2822
lr 0.00100000 - epoch 240 - loss: 2.4380
lr 0.00100000 - epoch 241 - loss: 2.6224
lr 0.00100000 - epoch 242 - loss: 2.6721
lr 0.00100000 - epoch 243 - loss: 1.8356
lr 0.00100000 - epoch 244 - loss: 2.0436
lr 0.00100000 - epoch 245 - loss: 3.4670
lr 0.00100000 - epoch 246 - loss: 2.8842
lr 0.00100000 - epoch 247 - loss: 2.1418
lr 0.00100000 - epoch 248 - loss: 1.9889
lr 0.00100000 - 

...

lr 0.00010000 - epoch 1698 - loss: 0.5274
lr 0.00010000 - epoch 1699 - loss: 0.5046
lr 0.00010000 - epoch 1700 - loss: 0.5211
lr 0.00010000 - epoch 1701 - loss: 0.5059
lr 0.00010000 - epoch 1702 - loss: 0.4861
lr 0.00010000 - epoch 1703 - loss: 0.5035
lr 0.00010000 - epoch 1704 - loss: 0.5091
lr 0.00010000 - epoch 1705 - loss: 0.5435
lr 0.00010000 - epoch 1706 - loss: 0.5209
lr 0.00010000 - epoch 1707 - loss: 0.4925
lr 0.00010000 - epoch 1708 - loss: 0.5254
lr 0.00010000 - epoch 1709 - loss: 0.5138
lr 0.00010000 - epoch 1710 - loss: 0.5185
lr 0.00010000 - epoch 1711 - loss: 0.5284
lr 0.00010000 - epoch 1712 - loss: 0.4904
lr 0.00010000 - epoch 1713 - loss: 0.4986
lr 0.00010000 - epoch 1714 - loss: 0.5006
lr 0.00010000 - epoch 1715 - loss: 0.5013
lr 0.00010000 - epoch 1716 - loss: 0.4985
lr 0.00010000 - epoch 1717 - loss: 0.5077
lr 0.00010000 - epoch 1718 - loss: 0.5112
lr 0.00010000 - epoch 1719 - loss: 0.5143
lr 0.00010000 - epoch 1720 - loss: 0.5095
lr 0.00010000 - epoch 1721 - loss:

lr 0.00010000 - epoch 1894 - loss: 0.5164
lr 0.00010000 - epoch 1895 - loss: 0.4724
lr 0.00010000 - epoch 1896 - loss: 0.5064
lr 0.00010000 - epoch 1897 - loss: 0.4879
lr 0.00010000 - epoch 1898 - loss: 0.5217
lr 0.00010000 - epoch 1899 - loss: 0.5325
lr 0.00010000 - epoch 1900 - loss: 0.5244
lr 0.00010000 - epoch 1901 - loss: 0.5156
lr 0.00010000 - epoch 1902 - loss: 0.5048
lr 0.00010000 - epoch 1903 - loss: 0.5066
lr 0.00010000 - epoch 1904 - loss: 0.5221
lr 0.00010000 - epoch 1905 - loss: 0.4845
lr 0.00010000 - epoch 1906 - loss: 0.5034
lr 0.00010000 - epoch 1907 - loss: 0.4991
lr 0.00010000 - epoch 1908 - loss: 0.5174
lr 0.00010000 - epoch 1909 - loss: 0.5372
lr 0.00010000 - epoch 1910 - loss: 0.5396
lr 0.00010000 - epoch 1911 - loss: 0.4992
lr 0.00010000 - epoch 1912 - loss: 0.4894
lr 0.00010000 - epoch 1913 - loss: 0.5034
lr 0.00010000 - epoch 1914 - loss: 0.5026
lr 0.00010000 - epoch 1915 - loss: 0.4944
lr 0.00010000 - epoch 1916 - loss: 0.4985
lr 0.00010000 - epoch 1917 - loss:

lr 0.00010000 - epoch 2091 - loss: 0.4588
lr 0.00010000 - epoch 2092 - loss: 0.4889
lr 0.00010000 - epoch 2093 - loss: 0.4638
lr 0.00010000 - epoch 2094 - loss: 0.4547
lr 0.00010000 - epoch 2095 - loss: 0.5033
lr 0.00010000 - epoch 2096 - loss: 0.4364
lr 0.00010000 - epoch 2097 - loss: 0.4329
lr 0.00010000 - epoch 2098 - loss: 0.4314
lr 0.00010000 - epoch 2099 - loss: 0.3942
lr 0.00010000 - epoch 2100 - loss: 0.4350
lr 0.00010000 - epoch 2101 - loss: 0.4548
lr 0.00010000 - epoch 2102 - loss: 0.4575
lr 0.00010000 - epoch 2103 - loss: 0.4871
lr 0.00010000 - epoch 2104 - loss: 0.4472
lr 0.00010000 - epoch 2105 - loss: 0.4675
lr 0.00010000 - epoch 2106 - loss: 0.4275
lr 0.00010000 - epoch 2107 - loss: 0.4524
lr 0.00010000 - epoch 2108 - loss: 0.4623
lr 0.00010000 - epoch 2109 - loss: 0.4636
lr 0.00010000 - epoch 2110 - loss: 0.4517
lr 0.00010000 - epoch 2111 - loss: 0.4254
lr 0.00010000 - epoch 2112 - loss: 0.4519
lr 0.00010000 - epoch 2113 - loss: 0.4353
lr 0.00010000 - epoch 2114 - loss:

lr 0.00010000 - epoch 2288 - loss: 0.4433
lr 0.00010000 - epoch 2289 - loss: 0.4308
lr 0.00010000 - epoch 2290 - loss: 0.4422
lr 0.00010000 - epoch 2291 - loss: 0.4300
lr 0.00010000 - epoch 2292 - loss: 0.4384
lr 0.00010000 - epoch 2293 - loss: 0.4341
lr 0.00010000 - epoch 2294 - loss: 0.4324
lr 0.00010000 - epoch 2295 - loss: 0.4537
lr 0.00010000 - epoch 2296 - loss: 0.4224
lr 0.00010000 - epoch 2297 - loss: 0.4364
lr 0.00010000 - epoch 2298 - loss: 0.4446
lr 0.00010000 - epoch 2299 - loss: 0.4246
lr 0.00010000 - epoch 2300 - loss: 0.4475
lr 0.00010000 - epoch 2301 - loss: 0.5035
lr 0.00010000 - epoch 2302 - loss: 0.4643
lr 0.00010000 - epoch 2303 - loss: 0.4771
lr 0.00010000 - epoch 2304 - loss: 0.4703
lr 0.00010000 - epoch 2305 - loss: 0.4703
lr 0.00010000 - epoch 2306 - loss: 0.4412
lr 0.00010000 - epoch 2307 - loss: 0.4353
lr 0.00010000 - epoch 2308 - loss: 0.4593
lr 0.00010000 - epoch 2309 - loss: 0.4673
lr 0.00010000 - epoch 2310 - loss: 0.4212
lr 0.00010000 - epoch 2311 - loss:

lr 0.00010000 - epoch 2484 - loss: 0.4448
lr 0.00010000 - epoch 2485 - loss: 0.4129
lr 0.00010000 - epoch 2486 - loss: 0.4458
lr 0.00010000 - epoch 2487 - loss: 0.4240
lr 0.00010000 - epoch 2488 - loss: 0.4411
lr 0.00010000 - epoch 2489 - loss: 0.4321
lr 0.00010000 - epoch 2490 - loss: 0.4274
lr 0.00010000 - epoch 2491 - loss: 0.4295
lr 0.00010000 - epoch 2492 - loss: 0.4123
lr 0.00010000 - epoch 2493 - loss: 0.4182
lr 0.00010000 - epoch 2494 - loss: 0.4262
lr 0.00010000 - epoch 2495 - loss: 0.4362
lr 0.00010000 - epoch 2496 - loss: 0.4103
lr 0.00010000 - epoch 2497 - loss: 0.4126
lr 0.00010000 - epoch 2498 - loss: 0.3909
lr 0.00010000 - epoch 2499 - loss: 0.3882


In [6]:
val_llKSGLD
#1e-3

array([[-2.21359706, -2.23083782, -2.16648412, -2.19140506, -2.25963783,
        -2.41003823, -2.24437475, -2.37945318, -2.62750483, -2.61576414]])

## K-SGFS

In [5]:
import torch
#import torchvision
import os

from itertools import chain
from torch import nn
#from torchvision import transforms
import torch.nn.functional as F
import numpy as np
#from numpy.random import RandomState

import ksgfs


np.random.seed(1)
torch.manual_seed(1)



batch_size = 32
dataset_size= 406

n_chains = 10
n_samples = 300


# learning_rates = [1e-2, 1e-3, 1e-4, 1e-5]
learning_rates = [9e-3, 8e-3, 7e-3, 6e-3, 5e-3, 4e-3, 3e-3, 2e-3, 1e-3, 9e-4, 8e-4, 7e-4, 6e-4, 5e-4, 4e-4, 3e-4, 2e-4, 1e-4]


val_llKSGFS = np.zeros((1,len(learning_rates)))

for i in range(1):
    for j,lr in enumerate(learning_rates):
        network = Model()
        criterion = nn.MSELoss(size_average=False)
        optim = ksgfs.optim.KSGFS(network, criterion, batch_size, dataset_size, eta=1., v=0., lambda_=1., epsilon=lr, l2=1e-3, invert_every=1)
        evaluate = evaluation(val_loader, n_samples, X_train_mean, X_train_std, y_train_mean, y_train_std)

        t = 1.
        n = 0


        for epoch in range(2500):
            running_loss = 0
            for x, y in iter(train_loader):
                x = x.view(x.size(0), -1)

                optim.update_curvature(x)

                network.zero_grad()
                output = network(x)
                loss = 0.5 * criterion(output, y)
                loss.backward()
                optim.step()

                running_loss += loss * batch_size / dataset_size

                if (t >= 300) & (t % 100 == 0) & (n < n_samples):
                    rmse, val_ll = evaluate.fn(network)
                    n += 1
                t += 1.
            print("lr {:.8f} - epoch {:d} - loss: {:.4f}".format(lr, epoch, running_loss))
#         val_resultsKSGFS[i,j] = rmse
        val_llKSGFS[i,j] = val_ll

/home/mojo/anaconda3/lib/python3.6/site-packages/torch/nn/functional.py:52: UserWarning: size_average and reduce args will be deprecated, please use reduction='sum' instead.
  warnings.warn(warning.format(ret))
/home/mojo/anaconda3/lib/python3.6/site-packages/torch/nn/functional.py:52: UserWarning: size_average and reduce args will be deprecated, please use reduction='none' instead.
  warnings.warn(warning.format(ret))


lr 0.00900000 - epoch 0 - loss: 9.7562
lr 0.00900000 - epoch 1 - loss: 8.7907
lr 0.00900000 - epoch 2 - loss: 6.1743
lr 0.00900000 - epoch 3 - loss: 6.1240
lr 0.00900000 - epoch 4 - loss: 8.0286
lr 0.00900000 - epoch 5 - loss: 4.3680
lr 0.00900000 - epoch 6 - loss: 4.6728
lr 0.00900000 - epoch 7 - loss: 5.4468
lr 0.00900000 - epoch 8 - loss: 4.3224
lr 0.00900000 - epoch 9 - loss: 3.4342
lr 0.00900000 - epoch 10 - loss: 4.7445
lr 0.00900000 - epoch 11 - loss: 4.2365
lr 0.00900000 - epoch 12 - loss: 3.5270
lr 0.00900000 - epoch 13 - loss: 4.5699
lr 0.00900000 - epoch 14 - loss: 3.0912
lr 0.00900000 - epoch 15 - loss: 2.6085
lr 0.00900000 - epoch 16 - loss: 2.5612
lr 0.00900000 - epoch 17 - loss: 2.2779
lr 0.00900000 - epoch 18 - loss: 3.6331
lr 0.00900000 - epoch 19 - loss: 2.6313
lr 0.00900000 - epoch 20 - loss: 3.0011
lr 0.00900000 - epoch 21 - loss: 2.6255
lr 0.00900000 - epoch 22 - loss: 3.4612


/home/mojo/anaconda3/lib/python3.6/site-packages/torch/nn/functional.py:52: UserWarning: size_average and reduce args will be deprecated, please use reduction='elementwise_mean' instead.
  warnings.warn(warning.format(ret))


lr 0.00900000 - epoch 23 - loss: 2.7658
lr 0.00900000 - epoch 24 - loss: 2.0265
lr 0.00900000 - epoch 25 - loss: 2.0349
lr 0.00900000 - epoch 26 - loss: 1.9097
lr 0.00900000 - epoch 27 - loss: 2.4390
lr 0.00900000 - epoch 28 - loss: 3.0607
lr 0.00900000 - epoch 29 - loss: 3.0513
lr 0.00900000 - epoch 30 - loss: 3.2702
lr 0.00900000 - epoch 31 - loss: 2.4792
lr 0.00900000 - epoch 32 - loss: 2.1161
lr 0.00900000 - epoch 33 - loss: 2.0904
lr 0.00900000 - epoch 34 - loss: 2.2429
lr 0.00900000 - epoch 35 - loss: 1.7898
lr 0.00900000 - epoch 36 - loss: 2.4420
lr 0.00900000 - epoch 37 - loss: 2.8556
lr 0.00900000 - epoch 38 - loss: 4.6774
lr 0.00900000 - epoch 39 - loss: 2.1052
lr 0.00900000 - epoch 40 - loss: 2.3875
lr 0.00900000 - epoch 41 - loss: 1.9939
lr 0.00900000 - epoch 42 - loss: 1.9068
lr 0.00900000 - epoch 43 - loss: 1.8918
lr 0.00900000 - epoch 44 - loss: 1.7765
lr 0.00900000 - epoch 45 - loss: 1.8759
lr 0.00900000 - epoch 46 - loss: 2.0257
lr 0.00900000 - epoch 47 - loss: 2.6812


lr 0.00900000 - epoch 225 - loss: 1.6174
lr 0.00900000 - epoch 226 - loss: 1.5605
lr 0.00900000 - epoch 227 - loss: 2.6154
lr 0.00900000 - epoch 228 - loss: 1.8733
lr 0.00900000 - epoch 229 - loss: 2.1484
lr 0.00900000 - epoch 230 - loss: 2.0893
lr 0.00900000 - epoch 231 - loss: 1.4143
lr 0.00900000 - epoch 232 - loss: 1.4874
lr 0.00900000 - epoch 233 - loss: 1.4407
lr 0.00900000 - epoch 234 - loss: 1.4419
lr 0.00900000 - epoch 235 - loss: 2.7229
lr 0.00900000 - epoch 236 - loss: 1.6917
lr 0.00900000 - epoch 237 - loss: 1.6119
lr 0.00900000 - epoch 238 - loss: 1.5467
lr 0.00900000 - epoch 239 - loss: 1.6334
lr 0.00900000 - epoch 240 - loss: 1.5806
lr 0.00900000 - epoch 241 - loss: 1.8973
lr 0.00900000 - epoch 242 - loss: 2.9418
lr 0.00900000 - epoch 243 - loss: 1.6940
lr 0.00900000 - epoch 244 - loss: 1.9137
lr 0.00900000 - epoch 245 - loss: 1.3450
lr 0.00900000 - epoch 246 - loss: 1.9332
lr 0.00900000 - epoch 247 - loss: 1.5039
lr 0.00900000 - epoch 248 - loss: 1.7896
lr 0.00900000 - 

...

lr 0.00010000 - epoch 1682 - loss: 0.8163
lr 0.00010000 - epoch 1683 - loss: 0.8806
lr 0.00010000 - epoch 1684 - loss: 0.9416
lr 0.00010000 - epoch 1685 - loss: 0.8424
lr 0.00010000 - epoch 1686 - loss: 0.8339
lr 0.00010000 - epoch 1687 - loss: 0.8410
lr 0.00010000 - epoch 1688 - loss: 0.8498
lr 0.00010000 - epoch 1689 - loss: 0.8401
lr 0.00010000 - epoch 1690 - loss: 0.9034
lr 0.00010000 - epoch 1691 - loss: 0.7993
lr 0.00010000 - epoch 1692 - loss: 0.8500
lr 0.00010000 - epoch 1693 - loss: 0.8928
lr 0.00010000 - epoch 1694 - loss: 0.9388
lr 0.00010000 - epoch 1695 - loss: 0.9275
lr 0.00010000 - epoch 1696 - loss: 0.8949
lr 0.00010000 - epoch 1697 - loss: 0.7926
lr 0.00010000 - epoch 1698 - loss: 0.8802
lr 0.00010000 - epoch 1699 - loss: 0.8284
lr 0.00010000 - epoch 1700 - loss: 0.7591
lr 0.00010000 - epoch 1701 - loss: 0.7745
lr 0.00010000 - epoch 1702 - loss: 0.8451
lr 0.00010000 - epoch 1703 - loss: 0.8286
lr 0.00010000 - epoch 1704 - loss: 0.8604
lr 0.00010000 - epoch 1705 - loss:

lr 0.00010000 - epoch 1878 - loss: 0.9644
lr 0.00010000 - epoch 1879 - loss: 0.9537
lr 0.00010000 - epoch 1880 - loss: 0.9039
lr 0.00010000 - epoch 1881 - loss: 0.8931
lr 0.00010000 - epoch 1882 - loss: 0.8418
lr 0.00010000 - epoch 1883 - loss: 0.9425
lr 0.00010000 - epoch 1884 - loss: 0.9808
lr 0.00010000 - epoch 1885 - loss: 0.9172
lr 0.00010000 - epoch 1886 - loss: 0.9191
lr 0.00010000 - epoch 1887 - loss: 0.8959
lr 0.00010000 - epoch 1888 - loss: 0.9942
lr 0.00010000 - epoch 1889 - loss: 0.8798
lr 0.00010000 - epoch 1890 - loss: 0.9181
lr 0.00010000 - epoch 1891 - loss: 0.8850
lr 0.00010000 - epoch 1892 - loss: 0.8626
lr 0.00010000 - epoch 1893 - loss: 0.8408
lr 0.00010000 - epoch 1894 - loss: 0.8226
lr 0.00010000 - epoch 1895 - loss: 0.8642
lr 0.00010000 - epoch 1896 - loss: 0.8962
lr 0.00010000 - epoch 1897 - loss: 0.8328
lr 0.00010000 - epoch 1898 - loss: 0.9199
lr 0.00010000 - epoch 1899 - loss: 0.9879
lr 0.00010000 - epoch 1900 - loss: 0.9634
lr 0.00010000 - epoch 1901 - loss:

lr 0.00010000 - epoch 2074 - loss: 0.8634
lr 0.00010000 - epoch 2075 - loss: 0.8075
lr 0.00010000 - epoch 2076 - loss: 0.8342
lr 0.00010000 - epoch 2077 - loss: 0.8824
lr 0.00010000 - epoch 2078 - loss: 0.7877
lr 0.00010000 - epoch 2079 - loss: 0.7841
lr 0.00010000 - epoch 2080 - loss: 0.8147
lr 0.00010000 - epoch 2081 - loss: 0.8412
lr 0.00010000 - epoch 2082 - loss: 0.8268
lr 0.00010000 - epoch 2083 - loss: 0.9546
lr 0.00010000 - epoch 2084 - loss: 0.8869
lr 0.00010000 - epoch 2085 - loss: 0.8697
lr 0.00010000 - epoch 2086 - loss: 0.8672
lr 0.00010000 - epoch 2087 - loss: 0.8867
lr 0.00010000 - epoch 2088 - loss: 0.8969
lr 0.00010000 - epoch 2089 - loss: 0.8914
lr 0.00010000 - epoch 2090 - loss: 0.7787
lr 0.00010000 - epoch 2091 - loss: 0.7939
lr 0.00010000 - epoch 2092 - loss: 0.9021
lr 0.00010000 - epoch 2093 - loss: 0.8799
lr 0.00010000 - epoch 2094 - loss: 0.7965
lr 0.00010000 - epoch 2095 - loss: 0.7972
lr 0.00010000 - epoch 2096 - loss: 0.8252
lr 0.00010000 - epoch 2097 - loss:

lr 0.00010000 - epoch 2271 - loss: 0.8230
lr 0.00010000 - epoch 2272 - loss: 0.7926
lr 0.00010000 - epoch 2273 - loss: 0.8431
lr 0.00010000 - epoch 2274 - loss: 0.9099
lr 0.00010000 - epoch 2275 - loss: 0.7871
lr 0.00010000 - epoch 2276 - loss: 0.8107
lr 0.00010000 - epoch 2277 - loss: 0.7806
lr 0.00010000 - epoch 2278 - loss: 0.7859
lr 0.00010000 - epoch 2279 - loss: 0.8213
lr 0.00010000 - epoch 2280 - loss: 0.7462
lr 0.00010000 - epoch 2281 - loss: 0.7610
lr 0.00010000 - epoch 2282 - loss: 0.8128
lr 0.00010000 - epoch 2283 - loss: 0.7896
lr 0.00010000 - epoch 2284 - loss: 0.7816
lr 0.00010000 - epoch 2285 - loss: 0.7229
lr 0.00010000 - epoch 2286 - loss: 0.7505
lr 0.00010000 - epoch 2287 - loss: 0.7606
lr 0.00010000 - epoch 2288 - loss: 0.7768
lr 0.00010000 - epoch 2289 - loss: 0.9226
lr 0.00010000 - epoch 2290 - loss: 0.7989
lr 0.00010000 - epoch 2291 - loss: 0.8609
lr 0.00010000 - epoch 2292 - loss: 0.8013
lr 0.00010000 - epoch 2293 - loss: 0.8167
lr 0.00010000 - epoch 2294 - loss:

lr 0.00010000 - epoch 2467 - loss: 0.8592
lr 0.00010000 - epoch 2468 - loss: 0.9568
lr 0.00010000 - epoch 2469 - loss: 0.7963
lr 0.00010000 - epoch 2470 - loss: 0.7836
lr 0.00010000 - epoch 2471 - loss: 0.7978
lr 0.00010000 - epoch 2472 - loss: 0.8866
lr 0.00010000 - epoch 2473 - loss: 0.9389
lr 0.00010000 - epoch 2474 - loss: 0.8789
lr 0.00010000 - epoch 2475 - loss: 0.8569
lr 0.00010000 - epoch 2476 - loss: 0.8420
lr 0.00010000 - epoch 2477 - loss: 0.8449
lr 0.00010000 - epoch 2478 - loss: 0.9034
lr 0.00010000 - epoch 2479 - loss: 0.8750
lr 0.00010000 - epoch 2480 - loss: 0.8759
lr 0.00010000 - epoch 2481 - loss: 0.8316
lr 0.00010000 - epoch 2482 - loss: 0.8579
lr 0.00010000 - epoch 2483 - loss: 0.8539
lr 0.00010000 - epoch 2484 - loss: 0.9345
lr 0.00010000 - epoch 2485 - loss: 0.8770
lr 0.00010000 - epoch 2486 - loss: 0.8671
lr 0.00010000 - epoch 2487 - loss: 0.8659
lr 0.00010000 - epoch 2488 - loss: 0.8473
lr 0.00010000 - epoch 2489 - loss: 0.7903
lr 0.00010000 - epoch 2490 - loss:

In [12]:
np.mean(val_resultsKSGFS,0)
#2e-2
#3e-2
#7e-3
#5e-4

array([2.7908823 , 2.58192053, 2.53662958, 2.51702113, 2.57709227,
       2.44274039, 2.53735542, 2.51817217])

In [6]:
val_llKSGFS
# 9e-3

array([[-2.30305338, -2.42509937, -2.3577764 , -2.63636255, -2.53086495,
        -2.60748982, -2.74621677, -2.46146226, -2.76939631, -2.58168364,
        -2.4795959 , -2.58314729, -2.60905266, -2.63116241, -2.67310476,
        -2.65296817, -2.71900606, -2.81619477]])